In [1]:
import gym
import numpy as np
import math
import random

In [3]:
env = gym.make('CartPole-v0')

In [4]:
env.action_space.n

2

In [5]:
env.observation_space

Box(-3.4028234663852886e+38, 3.4028234663852886e+38, (4,), float32)

In [40]:
NUM_BUCKETS = (1, 1, 6, 3)

In [7]:
NUM_ACTIONS = env.action_space.n

In [8]:
STATE_BOUNDS = list(zip(env.observation_space.low, env.observation_space.high))

In [9]:
STATE_BOUNDS

[(-4.8, 4.8),
 (-3.4028235e+38, 3.4028235e+38),
 (-0.41887903, 0.41887903),
 (-3.4028235e+38, 3.4028235e+38)]

In [10]:
STATE_BOUNDS[1] = [-0.5, 0.5]

In [11]:
STATE_BOUNDS[3] = [-math.radians(50), math.radians(50)]

In [12]:
STATE_BOUNDS

[(-4.8, 4.8),
 [-0.5, 0.5],
 (-0.41887903, 0.41887903),
 [-0.8726646259971648, 0.8726646259971648]]

In [42]:
q_table = np.zeros(NUM_BUCKETS + (NUM_ACTIONS,))

In [43]:
q_table

array([[[[[0., 0.],
          [0., 0.],
          [0., 0.]],

         [[0., 0.],
          [0., 0.],
          [0., 0.]],

         [[0., 0.],
          [0., 0.],
          [0., 0.]],

         [[0., 0.],
          [0., 0.],
          [0., 0.]],

         [[0., 0.],
          [0., 0.],
          [0., 0.]],

         [[0., 0.],
          [0., 0.],
          [0., 0.]]]]])

In [46]:
q_table.shape

(1, 1, 6, 3, 2)

In [23]:
EXPLORE_MIN_RATE = 0.01

In [20]:
LEARNING_MIN_RATE = 0.1 # alpha

In [19]:
def get_explore_rate(t):
    return max(EXPLORE_MIN_RATE, min(1, 1.0 - math.log10((t+1)/25)))

In [21]:
def get_learning_rate(t):
    return max(LEARNING_MIN_RATE, min(1, 1.0 - math.log10((t+1)/25)))

In [29]:
def select_action(state, explore_rate):
    if random.random() < explore_rate:
        action = env.action_space.sample()
    else:
        action = np.maxarg(q_table[state])
    return action

In [54]:
def state_of_bucket(state):
    bucket_indices = []
    for i in range(len(state)):
        if state[i] <= STATE_BOUNDS[i][0]:
            bucket_index = 0
        elif state[i] >= STATE_BOUNDS[i][1]:
            bucket_index = NUM_BUCKETS[i]-1
        else:
            bound_width = STATE_BOUNDS[i][1] - STATE_BOUNDS[i][0]
            offset = (NUM_BUCKETS[i]-1) * STATE_BOUNDS[i][0] / bound_width
            scalling = (NUM_BUCKETS[i]-1) / bound_width
            bucket_index = int(round(state[i]*scalling - offset))
        bucket_indices.append(bucket_index)
    return tuple(bucket_indices)

In [59]:
def simulate():
    learning_rate = get_learning_rate(0)
    explore_rate = get_explore_rate(0)
    discount_factor = 0.99 # gamma
    num_streaks = 0  # number of 200 times the cart has balanced pole
    for episode in range(1000):
        observ = env.reset()
        state_0 = state_of_bucket(observ)
        for t in range(250):  # 250 timesteps
            env.render()
            action = select_action(state_0, explore_rate)
            observ, reward, done, step = env.step(action)
            state = state_of_bucket(observ)
            print(state)
            best_q = np.amax(q_table[state]) # q learning, next best state
            q_table[state_0 + (action,)] = learning_rate * (reward + discount_factor * best_q - q_table[state_0 + (action,)])
            state_0 = state
            print(f'\nEpisode {episode}')
            print(f'time step {t}')
            print(f'Action {action}')
            print(f'State {state}')
            print(f'Reward {reward}')
            print(f'Best Q {best_q}')
            print(f'Explore rate {explore_rate}')
            print(f'Learning {learning_rate}')
            print(f'Streaks {num_streaks}')
            print('')
            
            if done:
                print(f'Episode {episode} is done after time steps {t}')
                if t >= 199:
                    num_streaks += 1
                else:
                    num_streaks = 0
                break
    

In [60]:
simulate()

(0, 0, 2, 1)

Episode 0
time step 0
Action 1
State (0, 0, 2, 1)
Reward 1.0
Best Q 0.0
Explore rate 1
Learning 1
Streaks 0

(0, 0, 2, 1)

Episode 0
time step 1
Action 0
State (0, 0, 2, 1)
Reward 1.0
Best Q 1.0
Explore rate 1
Learning 1
Streaks 0

(0, 0, 2, 1)

Episode 0
time step 2
Action 0
State (0, 0, 2, 1)
Reward 1.0
Best Q 1.99
Explore rate 1
Learning 1
Streaks 0

(0, 0, 2, 1)

Episode 0
time step 3
Action 1
State (0, 0, 2, 1)
Reward 1.0
Best Q 1.0
Explore rate 1
Learning 1
Streaks 0

(0, 0, 2, 1)

Episode 0
time step 4
Action 1
State (0, 0, 2, 1)
Reward 1.0
Best Q 0.99
Explore rate 1
Learning 1
Streaks 0

(0, 0, 2, 0)

Episode 0
time step 5
Action 1
State (0, 0, 2, 0)
Reward 1.0
Best Q 0.0
Explore rate 1
Learning 1
Streaks 0

(0, 0, 2, 0)

Episode 0
time step 6
Action 1
State (0, 0, 2, 0)
Reward 1.0
Best Q 0.0
Explore rate 1
Learning 1
Streaks 0

(0, 0, 2, 0)

Episode 0
time step 7
Action 0
State (0, 0, 2, 0)
Reward 1.0
Best Q 1.0
Explore rate 1
Learning 1
Streaks 0

(0, 0, 2, 0)



(0, 0, 3, 2)

Episode 3
time step 4
Action 0
State (0, 0, 3, 2)
Reward 1.0
Best Q 1.9701
Explore rate 1
Learning 1
Streaks 0

(0, 0, 3, 2)

Episode 3
time step 5
Action 1
State (0, 0, 3, 2)
Reward 1.0
Best Q 3.940399
Explore rate 1
Learning 1
Streaks 0

(0, 0, 3, 1)

Episode 3
time step 6
Action 1
State (0, 0, 3, 1)
Reward 1.0
Best Q 3.930499
Explore rate 1
Learning 1
Streaks 0

(0, 0, 3, 2)

Episode 3
time step 7
Action 0
State (0, 0, 3, 2)
Reward 1.0
Best Q 3.940399
Explore rate 1
Learning 1
Streaks 0

(0, 0, 3, 2)

Episode 3
time step 8
Action 0
State (0, 0, 3, 2)
Reward 1.0
Best Q 3.940399
Explore rate 1
Learning 1
Streaks 0

(0, 0, 3, 2)

Episode 3
time step 9
Action 1
State (0, 0, 3, 2)
Reward 1.0
Best Q 1.9602989999999987
Explore rate 1
Learning 1
Streaks 0

(0, 0, 3, 2)

Episode 3
time step 10
Action 1
State (0, 0, 3, 2)
Reward 1.0
Best Q 0.9803970099999999
Explore rate 1
Learning 1
Streaks 0

(0, 0, 3, 1)

Episode 3
time step 11
Action 1
State (0, 0, 3, 1)
Reward 1.0
Best Q 1.

(0, 0, 2, 1)

Episode 4
time step 11
Action 1
State (0, 0, 2, 1)
Reward 1.0
Best Q 0.9901997011278898
Explore rate 1
Learning 1
Streaks 0

(0, 0, 2, 0)

Episode 4
time step 12
Action 1
State (0, 0, 2, 0)
Reward 1.0
Best Q 1.0001852255544494
Explore rate 1
Learning 1
Streaks 0

(0, 0, 2, 1)

Episode 4
time step 13
Action 0
State (0, 0, 2, 1)
Reward 1.0
Best Q 1.0000853703101837
Explore rate 1
Learning 1
Streaks 0

(0, 0, 2, 1)

Episode 4
time step 14
Action 0
State (0, 0, 2, 1)
Reward 1.0
Best Q 1.0000853703101837
Explore rate 1
Learning 1
Streaks 0

(0, 0, 2, 1)

Episode 4
time step 15
Action 0
State (0, 0, 2, 1)
Reward 1.0
Best Q 1.0000853703101837
Explore rate 1
Learning 1
Streaks 0

(0, 0, 2, 1)

Episode 4
time step 16
Action 1
State (0, 0, 2, 1)
Reward 1.0
Best Q 1.0000853703101837
Explore rate 1
Learning 1
Streaks 0

(0, 0, 2, 1)

Episode 4
time step 17
Action 1
State (0, 0, 2, 1)
Reward 1.0
Best Q 0.9900990199000002
Explore rate 1
Learning 1
Streaks 0

(0, 0, 2, 0)

Episode 4
tim

(0, 0, 3, 1)

Episode 7
time step 2
Action 0
State (0, 0, 3, 1)
Reward 1.0
Best Q 1.883248652348435
Explore rate 1
Learning 1
Streaks 0

(0, 0, 3, 1)

Episode 7
time step 3
Action 1
State (0, 0, 3, 1)
Reward 1.0
Best Q 1.8745091409339572
Explore rate 1
Learning 1
Streaks 0

(0, 0, 3, 1)

Episode 7
time step 4
Action 0
State (0, 0, 3, 1)
Reward 1.0
Best Q 0.9812549085906603
Explore rate 1
Learning 1
Streaks 0

(0, 0, 3, 1)

Episode 7
time step 5
Action 1
State (0, 0, 3, 1)
Reward 1.0
Best Q 0.9902748460282382
Explore rate 1
Learning 1
Streaks 0

(0, 0, 3, 1)

Episode 7
time step 6
Action 0
State (0, 0, 3, 1)
Reward 1.0
Best Q 0.9991171889772956
Explore rate 1
Learning 1
Streaks 0

(0, 0, 3, 2)

Episode 7
time step 7
Action 0
State (0, 0, 3, 2)
Reward 1.0
Best Q 0.9995337935885695
Explore rate 1
Learning 1
Streaks 0

(0, 0, 3, 2)

Episode 7
time step 8
Action 0
State (0, 0, 3, 2)
Reward 1.0
Best Q 0.9995337935885695
Explore rate 1
Learning 1
Streaks 0

(0, 0, 3, 2)

Episode 7
time step 9

(0, 0, 2, 1)

Episode 9
time step 16
Action 0
State (0, 0, 2, 1)
Reward 1.0
Best Q 1.9597357267750726
Explore rate 1
Learning 1
Streaks 0

(0, 0, 2, 2)

Episode 9
time step 17
Action 0
State (0, 0, 2, 2)
Reward 1.0
Best Q 1.9801009801980098
Explore rate 1
Learning 1
Streaks 0

(0, 0, 2, 1)

Episode 9
time step 18
Action 1
State (0, 0, 2, 1)
Reward 1.0
Best Q 1.9798973276637806
Explore rate 1
Learning 1
Streaks 0

(0, 0, 3, 2)

Episode 9
time step 19
Action 0
State (0, 0, 3, 2)
Reward 1.0
Best Q 0.9900000878644977
Explore rate 1
Learning 1
Streaks 0

(0, 0, 3, 2)

Episode 9
time step 20
Action 0
State (0, 0, 3, 2)
Reward 1.0
Best Q 0.9900000878644977
Explore rate 1
Learning 1
Streaks 0

(0, 0, 3, 2)

Episode 9
time step 21
Action 1
State (0, 0, 3, 2)
Reward 1.0
Best Q 0.9997030494758616
Explore rate 1
Learning 1
Streaks 0

(0, 0, 3, 2)

Episode 9
time step 22
Action 0
State (0, 0, 3, 2)
Reward 1.0
Best Q 0.9997059311166052
Explore rate 1
Learning 1
Streaks 0

(0, 0, 3, 2)

Episode 9
tim

...

(0, 0, 2, 0)

Episode 990
time step 4
Action 1
State (0, 0, 2, 0)
Reward 1.0
Best Q 0.9900990111891299
Explore rate 1
Learning 1
Streaks 0

(0, 0, 2, 0)

Episode 990
time step 5
Action 1
State (0, 0, 2, 0)
Reward 1.0
Best Q 0.9900990110412784
Explore rate 1
Learning 1
Streaks 0

(0, 0, 2, 0)

Episode 990
time step 6
Action 1
State (0, 0, 2, 0)
Reward 1.0
Best Q 0.9900990110427568
Explore rate 1
Learning 1
Streaks 0

(0, 0, 1, 0)

Episode 990
time step 7
Action 0
State (0, 0, 1, 0)
Reward 1.0
Best Q 1.007829525201202
Explore rate 1
Learning 1
Streaks 0

(0, 0, 1, 0)

Episode 990
time step 8
Action 0
State (0, 0, 1, 0)
Reward 1.0
Best Q 1.007829525201202
Explore rate 1
Learning 1
Streaks 0

Episode 990 is done after time steps 8
(0, 0, 2, 1)

Episode 991
time step 0
Action 1
State (0, 0, 2, 1)
Reward 1.0
Best Q 1.0298575448129192
Explore rate 1
Learning 1
Streaks 0

(0, 0, 2, 0)

Episode 991
time step 1
Action 1
State (0, 0, 2, 0)
Reward 1.0
Best Q 1.0076522189079116
Explore rate 1
Learn

(0, 0, 3, 2)

Episode 993
time step 17
Action 1
State (0, 0, 3, 2)
Reward 1.0
Best Q 0.9901037158003034
Explore rate 1
Learning 1
Streaks 0

(0, 0, 3, 2)

Episode 993
time step 18
Action 1
State (0, 0, 3, 2)
Reward 1.0
Best Q 0.9901037162756696
Explore rate 1
Learning 1
Streaks 0

(0, 0, 3, 1)

Episode 993
time step 19
Action 1
State (0, 0, 3, 1)
Reward 1.0
Best Q 0.9901122057487086
Explore rate 1
Learning 1
Streaks 0

(0, 0, 3, 2)

Episode 993
time step 20
Action 0
State (0, 0, 3, 2)
Reward 1.0
Best Q 0.9901121208539785
Explore rate 1
Learning 1
Streaks 0

(0, 0, 4, 2)

Episode 993
time step 21
Action 0
State (0, 0, 4, 2)
Reward 1.0
Best Q 0.9900990092059889
Explore rate 1
Learning 1
Streaks 0

(0, 0, 4, 2)

Episode 993
time step 22
Action 0
State (0, 0, 4, 2)
Reward 1.0
Best Q 0.9900990092059889
Explore rate 1
Learning 1
Streaks 0

(0, 0, 4, 2)

Episode 993
time step 23
Action 1
State (0, 0, 4, 2)
Reward 1.0
Best Q 0.9900990099079401
Explore rate 1
Learning 1
Streaks 0

Episode 993 i

(0, 0, 3, 1)

Episode 996
time step 6
Action 1
State (0, 0, 3, 1)
Reward 1.0
Best Q 0.9901295959760918
Explore rate 1
Learning 1
Streaks 0

(0, 0, 3, 0)

Episode 996
time step 7
Action 1
State (0, 0, 3, 0)
Reward 1.0
Best Q 1.635051592924021
Explore rate 1
Learning 1
Streaks 0

(0, 0, 3, 1)

Episode 996
time step 8
Action 0
State (0, 0, 3, 1)
Reward 1.0
Best Q 1.6285888735343086
Explore rate 1
Learning 1
Streaks 0

(0, 0, 3, 0)

Episode 996
time step 9
Action 1
State (0, 0, 3, 0)
Reward 1.0
Best Q 0.9772513918749446
Explore rate 1
Learning 1
Streaks 0

(0, 0, 3, 0)

Episode 996
time step 10
Action 1
State (0, 0, 3, 0)
Reward 1.0
Best Q 0.9772513918749446
Explore rate 1
Learning 1
Streaks 0

(0, 0, 3, 1)

Episode 996
time step 11
Action 0
State (0, 0, 3, 1)
Reward 1.0
Best Q 0.9901295959760918
Explore rate 1
Learning 1
Streaks 0

(0, 0, 3, 1)

Episode 996
time step 12
Action 0
State (0, 0, 3, 1)
Reward 1.0
Best Q 0.9901295959760918
Explore rate 1
Learning 1
Streaks 0

(0, 0, 3, 1)

Epis

(0, 0, 2, 1)

Episode 998
time step 10
Action 0
State (0, 0, 2, 1)
Reward 1.0
Best Q 0.9901030062152201
Explore rate 1
Learning 1
Streaks 0

(0, 0, 2, 1)

Episode 998
time step 11
Action 0
State (0, 0, 2, 1)
Reward 1.0
Best Q 0.9900989699378477
Explore rate 1
Learning 1
Streaks 0

(0, 0, 2, 2)

Episode 998
time step 12
Action 0
State (0, 0, 2, 2)
Reward 1.0
Best Q 0.9908842901485382
Explore rate 1
Learning 1
Streaks 0

(0, 0, 2, 2)

Episode 998
time step 13
Action 0
State (0, 0, 2, 2)
Reward 1.0
Best Q 0.9908842901485382
Explore rate 1
Learning 1
Streaks 0

(0, 0, 2, 2)

Episode 998
time step 14
Action 0
State (0, 0, 2, 2)
Reward 1.0
Best Q 0.9912803680045414
Explore rate 1
Learning 1
Streaks 0

(0, 0, 3, 2)

Episode 998
time step 15
Action 0
State (0, 0, 3, 2)
Reward 1.0
Best Q 0.9901576761219231
Explore rate 1
Learning 1
Streaks 0

(0, 0, 3, 2)

Episode 998
time step 16
Action 1
State (0, 0, 3, 2)
Reward 1.0
Best Q 0.9901576761219231
Explore rate 1
Learning 1
Streaks 0

(0, 0, 3, 2)


(0, 0, 4, 1)

Episode 999
time step 23
Action 1
State (0, 0, 4, 1)
Reward 1.0
Best Q 0.9900990084826198
Explore rate 1
Learning 1
Streaks 0

Episode 999 is done after time steps 23


In [47]:
env.close()

array([0., 0.])

In [53]:
q_table

array([0., 0.])